In [325]:
import numpy as np
import pandas as pd
import lightgbm as lgbm
import os
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime
import time
from sklearn.linear_model import LinearRegression
from tqdm import tqdm_notebook as tqdm

In [2]:
def smape(satellite_predicted_values, satellite_true_values): 
    # the division, addition and subtraction are pointwise 
    return np.mean(np.abs((satellite_predicted_values - satellite_true_values) 
        / (np.abs(satellite_predicted_values) + np.abs(satellite_true_values))))

In [28]:
# Загрузка данных
# windows
PATH_TO_DATA = os.path.join('C:\\', 'Users', '79242', 'Documents', 'Sandbox', 'IDAO')
full_train = pd.read_csv(os.path.join(PATH_TO_DATA, 'train.csv'), index_col='id')
full_test = pd.read_csv(os.path.join(PATH_TO_DATA, 'test.csv'), index_col='id')

In [29]:
full_train

epoch  sat_id             x             y  \
id                                                                     
0        2014-01-01T00:00:00.000       0  -8855.823863  13117.780146   
1        2014-01-01T00:46:43.000       0 -10567.672384   1619.746066   
2        2014-01-01T01:33:26.001       0 -10578.684043 -10180.467460   
3        2014-01-01T02:20:09.001       0  -9148.251857 -20651.437460   
4        2014-01-01T03:06:52.002       0  -6719.092336 -28929.061629   
...                          ...     ...           ...           ...   
1234089  2014-01-31T22:00:22.602     599 -21721.485878 -14048.557595   
1234090  2014-01-31T22:25:13.240     599 -23176.890569  -8712.016936   
1234091  2014-01-31T22:50:03.878     599 -23363.044794  -2906.071320   
1234092  2014-01-31T23:14:54.515     599 -22058.020262   3074.894039   
1234093  2014-01-31T23:39:45.153     599 -19076.969715   8807.476785   

                    z        Vx        Vy        Vz         x_sim  \
id                                                                  
0       -20728.353233 -0.908303 -3.808436 -2.022083  -8843.131454   
1       -24451.813271 -0.302590 -4.272617 -0.612796 -10555.500066   
2       -24238.280949  0.277435 -4.047522  0.723155 -10571.858472   
3       -20720.381279  0.715600 -3.373762  1.722115  -9149.620794   
4       -14938.907967  0.992507 -2.519732  2.344703  -6729.358857   
...               ...       ...       ...       ...           ...   
1234089   5277.807430 -1.351754  3.373418  0.004995 -20717.958996   
1234090   5153.371350 -0.575955  3.764450 -0.175109 -22673.444496   
1234091   4747.247386  0.351381  3.992943 -0.372198 -23461.830699   
1234092   4038.853542  1.421085  3.984793 -0.578849 -22858.679929   
1234093   3024.623998  2.587973  3.641717 -0.778817 -20656.328603   

                y_sim         z_sim    Vx_sim    Vy_sim    Vz_sim  
id                                                                 
0        13138.221690 -20741.615306 -0.907527 -3.804930 -2.024133  
1         1649.289367 -24473.089556 -0.303704 -4.269816 -0.616468  
2       -10145.939908 -24271.169776  0.274880 -4.046788  0.718768  
3       -20618.200201 -20765.019094  0.712437 -3.375202  1.718306  
4       -28902.271436 -14992.399986  0.989382 -2.522618  2.342237  
...               ...           ...       ...       ...       ...  
1234089 -16245.240500   5250.939232 -1.653931  3.157321  0.079069  
1234090 -11192.339393   5243.608790 -0.945328  3.603371 -0.092202  
1234091  -5570.167175   4966.813869 -0.087089  3.912550 -0.281989  
1234092    373.249102   4396.055679  0.920162  4.021955 -0.485364  
1234093   6277.934683   3518.642806  2.050990  3.844021 -0.690707  

[649912 rows x 14 columns]

In [30]:
full_test

sat_id                    epoch         x_sim         y_sim  \
id                                                                     
3927          1  2014-02-01T00:01:45.162 -13366.891347 -14236.753503   
3928          1  2014-02-01T00:22:57.007  -7370.434039 -14498.771520   
3929          1  2014-02-01T00:44:08.852   -572.068654 -13065.289498   
3930          1  2014-02-01T01:05:20.697   6208.945257  -9076.852425   
3931          1  2014-02-01T01:26:32.542  10768.200284  -2199.706707   
...         ...                      ...           ...           ...   
1231060     597  2014-02-28T05:19:01.386  28595.031634 -85458.623976   
1231061     597  2014-02-28T07:21:46.454  15547.173728 -84233.509948   
1231062     597  2014-02-28T09:24:31.522   1981.107111 -80123.860051   
1231063     597  2014-02-28T11:27:16.590 -11644.801379 -72674.504171   
1231064     597  2014-02-28T13:30:01.658 -24606.415254 -61329.599053   

               z_sim    Vx_sim    Vy_sim    Vz_sim  
id                                                  
3927     6386.774555  4.333815 -0.692764  0.810774  
3928     7130.411325  5.077413  0.360609  0.313402  
3929     7033.794876  5.519106  2.012830 -0.539412  
3930     5548.296900  4.849212  4.338955 -1.869600  
3931     2272.014862  1.940505  6.192887 -3.167724  
...              ...       ...       ...       ...  
1231060  5021.767767 -1.721131 -0.011611  0.122357  
1231061  5840.616702 -1.815323  0.353445  0.098927  
1231062  6458.394351 -1.858963  0.773846  0.067379  
1231063  6805.361999 -1.826030  1.262930  0.024782  
1231064  6784.763455 -1.667849  1.833746 -0.033371  

[284071 rows x 8 columns]

In [34]:
full_train.groupby('sat_id').describe().T

sat_id                 0             1             2             3    \
x      count    958.000000   2108.000000    417.000000    354.000000   
       mean    4900.339540 -16110.661352 -35645.536202  55850.315483   
       std     9843.287489  13802.803673  40448.660925  42226.892159   
       min   -10752.229751 -33092.618399 -83475.871225 -28036.656341   
       25%    -4846.044039 -28724.877108 -72080.483505  27794.354266   
...                    ...           ...           ...           ...   
Vz_sim min       -3.582274     -3.267208     -2.548670     -0.070043   
       25%       -2.024101     -0.877540     -0.768268     -0.058169   
       50%        0.714230      0.572531      0.423172     -0.028103   
       75%        2.176876      1.214693      0.889922      0.039338   
       max        2.752681      1.472417      1.036697      0.214409   

sat_id                 4             5             6              7    \
x      count   1210.000000   3531.000000    418.000000     235.000000   
       mean   -6362.637373  -1332.440347  -3992.980574  -69315.624667   
       std    20304.954487  10516.767043  40254.674362   54817.363085   
       min   -33119.544128 -15784.759280 -65975.489409 -130892.958010   
       25%   -26239.094949 -11832.997586 -44257.957384 -119053.574244   
...                    ...           ...           ...            ...   
Vz_sim min       -3.853693     -0.573519     -1.695279      -0.856612   
       25%       -2.220249     -0.388132     -1.125444      -0.702429   
       50%        0.270589      0.011565     -0.117304      -0.328873   
       75%        1.967847      0.387142      0.980571       0.378398   
       max        2.712233      0.540706      1.592432       2.509000   

sat_id                 8             9    ...           590           591  \
x      count   2578.000000    330.000000  ...    584.000000    339.000000   
       mean    1821.125809   3974.751573  ...  33969.821907 -46291.314162   
       std    12760.325326  43704.812113  ...  32899.164658  45188.396733   
       min   -16973.914939 -59286.173946  ... -26260.593295 -98305.756377   
       25%   -10903.902531 -38957.735073  ...   3605.024327 -85473.827246   
...                    ...           ...  ...           ...           ...   
Vz_sim min       -4.264669     -0.960054  ...     -1.970567     -1.991123   
       25%       -3.156244     -0.726537  ...     -0.586607     -0.526903   
       50%       -0.245740     -0.170071  ...      0.286695      0.286162   
       75%        2.833273      0.738587  ...      0.669490      0.629948   
       max        4.760241      1.670801  ...      0.765256      0.720292   

sat_id                 592           593           594           595  \
x      count   1281.000000   1307.000000   1210.000000    499.000000   
       mean  -21555.015684  -8668.628135  -1425.664933  10580.871178   
       std    19364.957099  20257.571491  20617.707887  12574.760713   
       min   -46535.764661 -34693.709309 -30089.826690 -11853.697706   
       25%   -39108.560422 -27242.692225 -23186.033247   -138.602966   
...                    ...           ...           ...           ...   
Vz_sim min       -0.739670     -1.813285     -0.592408     -1.481722   
       25%       -0.343957     -1.438917     -0.479257     -1.353386   
       50%        0.071640     -0.263998     -0.093983     -0.831555   
       75%        0.373128      1.429139      0.467210      0.375542   
       max        0.526760      2.734514      0.916017      4.522846   

sat_id                 596           597           598           599  
x      count    378.000000    366.000000    648.000000   1797.000000  
       mean  -46606.855632  31587.704549  -9840.325692  -1249.927953  
       std    41480.443911  44511.927815  30444.932286  15884.479675  
       min   -93502.440554 -42789.959911 -50041.240812 -23364.288658  
       25%   -85035.962802 -10270.594276 -39882.598904 -16966.877633  
...                    ...           ...  

In [40]:
# захотел посмотреть разницу в значениях для SGP-4 и реальными данными
# типо много на смом деле пздц как сильно разнятся данные
for col_name in full_train.columns[2:8]:
    full_train['delta_' + col_name] = full_train[col_name + '_sim'] - full_train[col_name]

In [52]:
delta_names = full_train.columns[14:].to_list()
full_train[delta_names + ['sat_id']].groupby('sat_id').describe().T

sat_id                   0             1             2             3    \
delta_x  count    958.000000   2108.000000    417.000000    354.000000   
         mean       1.208894   2112.446451    209.738936    326.081733   
         std     3053.526207   3023.693121   8822.708298   9808.638586   
         min    -9158.649797  -6436.183200 -14920.301581 -14903.045100   
         25%    -1828.329475    356.937143  -5421.606604  -6001.735250   
         50%       -8.945639   1152.946981    128.041125    383.232946   
         75%     2282.419198   2726.027123   2288.651543   1527.084463   
         max     6917.312123  17367.556899  19390.882441  28777.855432   
delta_y  count    958.000000   2108.000000    417.000000    354.000000   
         mean     116.593133    967.435361    270.342042    462.127083   
         std     7597.380352   2587.474040   7227.142785   9252.314910   
         min   -24606.996844  -3844.271797  -9009.900653 -10312.501834   
         25%    -1855.298718   -377.008210  -5540.713615  -6055.279076   
         50%       60.570556    291.688607    197.468144    383.885947   
         75%     5880.063383   1868.422009    559.467311    752.844230   
         max    15717.764473  15730.765773  19903.429995  34502.645265   
delta_z  count    958.000000   2108.000000    417.000000    354.000000   
         mean      22.924476   -495.756239   -241.054095     73.990910   
         std     7049.800675   1218.497508   5640.607478    398.319301   
         min   -20854.343912  -9279.725634 -16018.333741   -275.256608   
         25%    -3969.392231   -658.088749   -471.811997   -198.265860   
         50%       -0.939923   -149.805171    -94.164479    -42.036419   
         75%     5203.577582    155.601082   4185.588866    172.396305   
         max    16136.676476   1191.359434   6474.836888   1626.763089   
delta_Vx count    958.000000   2108.000000    417.000000    354.000000   
         mean      -0.004689      0.005204     -0.002586     -0.000300   
         std        0.315299      1.006593      0.476247      0.653900   
         min       -0.566125     -7.131834     -1.794321     -0.851062   
         25%       -0.218022     -0.032449     -0.000997     -0.199196   
         50%       -0.005414      0.161538      0.010094     -0.063781   
         75%        0.017119      0.415207      0.287958      0.001899   
         max        1.255503      1.854253      0.433711      3.500176   
delta_Vy count    958.000000   2108.000000    417.000000    354.000000   
         mean       0.006447     -0.001392      0.001843      0.001055   
         std        0.785378      0.840887      0.392098      0.641630   
         min       -2.816411     -3.771695     -0.711624     -3.200847   
         25%       -0.156618     -0.326897     -0.166890     -0.002824   
         50%        0.006186     -0.132941     -0.005574      0.012887   
         75%        0.496491      0.039716      0.017807      0.146086   
         max        1.811752      4.890861      1.222634      1.449138   
delta_Vz count    958.000000   2108.000000    417.000000    354.000000   
         mean      -0.010981     -0.000087     -0.000434      0.000018   
         std        0.727671      0.459331      0.307920      0.029601   
         min       -1.280543     -2.517144     -0.754185     -0.077633   
         25%       -0.489488     -0.079877     -0.076514     -0.006506   
         50%       -0.013991     -0.001470     -0.001790     -0.000712   
         75%        0.038134      0.039206      0.050767      0.003000   
         max        2.904666      2.851689      0.815040      0.136409   

sat_id                   4            5             6             7    \
delta_x  count   1210.000000  3531.000000    418.000000    235.000000   
         mean       8.249695   -12.821916 -13515.094036    449.078722   
         std    10555.451555  1904.838397  18191.192960  21917.512787   
         min   -18287.374618 -4595.159437 -77497.609193 -39129.842720   
        

In [219]:
# отрисовка нужного рядя для анализа

figure = plt.figure(figsize=(10, 5))


sat_id = 28
real_col_name = 'x'
sim_col_name = real_col_name + '_sim'

fig = go.Figure()
fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][real_col_name],
                         name="Real",
                         line_color='deepskyblue'))

fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][sim_col_name],
                         name="Simulation",
                         line_color='dimgray'))

fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                         y=full_test[full_test.sat_id == sat_id][sim_col_name],
                         name="Sim_test",
                         line_color='MediumPurple'))

fig.update_layout(title_text='Time Series for ' + real_col_name,
                  xaxis_rangeslider_visible=True,
                  yaxis_title=real_col_name)
fig.show()

<Figure size 720x360 with 0 Axes>

In [245]:
# короче sim данные дофига тупые до 225 минут там вроде в задаче написано, нам надо бы предскзаать это дерьмо
# надо проверить гипотезу о периодах

figure = plt.figure(figsize=(10, 5))


sat_id = 113
real_col_name = 'x'
sim_col_name = real_col_name + '_sim'

df_train = full_train[full_train.sat_id == sat_id]
df_test = full_test[full_test.sat_id == sat_id]

d_real = df_train[real_col_name].values
d_sim = df_train[sim_col_name].values
d_test = df_test[sim_col_name].values

fig = go.Figure()
fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][real_col_name],
                         name="Real",
                         line_color='deepskyblue'))

fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][sim_col_name],
                         name="Simulation",
                         line_color='dimgray'))

fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                         y=full_test[full_test.sat_id == sat_id][sim_col_name],
                         name="Sim_test",
                         line_color='MediumPurple'))

fig.update_layout(title_text='Time Series for ' + real_col_name,
                  xaxis_rangeslider_visible=True,
                  yaxis_title=real_col_name)
fig.show()

<Figure size 720x360 with 0 Axes>

In [274]:
# интерполяция по производной !!! просто интересно было псомотерть


sat_id = 33
fig = make_subplots(rows=3, cols=2,
                    subplot_titles=['x', 'Vx', 'y', 'Vy', 'z', 'Vz'])

for i, real_col_name in enumerate(['x', 'y', 'z', 'Vx', 'Vy', 'Vz']):
    row, col = i % 3 + 1, i // 3 + 1
    sim_col_name = real_col_name + '_sim'
    fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                             y=full_train[full_train.sat_id == sat_id][real_col_name],
                             name="Real " + real_col_name,
                             ), row=row, col=col)

    fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                             y=full_train[full_train.sat_id == sat_id][sim_col_name],
                             name="Simulation " + real_col_name,
                             ), row=row, col=col)

    fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                             y=full_test[full_test.sat_id == sat_id][sim_col_name],
                             name="Sim_test " + real_col_name,
                             ), row=row, col=col)
fig.show()

In [ ]:


sat_id = 28

real_col_name = 'x'
sim_col_name = real_col_name + '_sim'

df_train = full_train[full_train.sat_id == sat_id]
df_test = full_test[full_test.sat_id == sat_id]

d_t = df_train.epoch.apply(lambda x: time.mktime(datetime.strptime(x, '%Y-%m-%dT%H:%M:%S.%f').timetuple())).values
d_t = d_t[1:] - d_t[:-1]
d_t[d_t == 0] = 10000

d_tt = df_test.epoch.apply(lambda x: time.mktime(datetime.strptime(x, '%Y-%m-%dT%H:%M:%S.%f').timetuple())).values
d_tt = d_tt[1:] - d_tt[:-1]
d_tt[d_tt == 0] = 10000

d_real = full_train[full_train.sat_id == sat_id][real_col_name].values[1:] - full_train[full_train.sat_id == sat_id][real_col_name].values[:-1]
d_sim = full_train[full_train.sat_id == sat_id][sim_col_name].values[1:] - full_train[full_train.sat_id == sat_id][sim_col_name].values[:-1]
d_test = full_test[full_test.sat_id == sat_id][sim_col_name].values[1:] - full_test[full_test.sat_id == sat_id][sim_col_name].values[:-1]

fig = go.Figure()
fig.add_trace(go.Scatter(x=df_train.epoch.values[1:],
                         y=d_real / d_t,
                         name="Real",
                         line_color='deepskyblue'))

fig.add_trace(go.Scatter(x=df_train.epoch.values[1:],
                         y=d_sim / d_t,
                         name="Simulation",
                         line_color='dimgray'))

fig.add_trace(go.Scatter(x=df_test.epoch.values[1:],
                         y=d_test / d_tt,
                         name="Sim_test",
                         line_color='MediumPurple'))

fig.update_layout(title_text='Time Series for ' + real_col_name,
                  xaxis_rangeslider_visible=True,
                  yaxis_title=real_col_name)
fig.show()

In [251]:
# посчитаем основные статистики и закинем их как признаки хотя конечно
# странно вообще предсказывать временные ряды с помощью деревьев
# получается что 24 точки это период!
# давайте сделаем следующее - найдём минимум или максимум,
# чтобы найти нижнюю или верхнюю точку периода
# а далее будем считать по ним статистики

# ничего плохого в том, чтобы использовать простые модели для каждого спутника


In [275]:
# от каждого спутника мы берём первые 24 значения ищем минимум по каждой колонке

epoch  sat_id             x             y  \
id                                                                     
0        2014-01-01T00:00:00.000       0  -8855.823863  13117.780146   
1        2014-01-01T00:46:43.000       0 -10567.672384   1619.746066   
2        2014-01-01T01:33:26.001       0 -10578.684043 -10180.467460   
3        2014-01-01T02:20:09.001       0  -9148.251857 -20651.437460   
4        2014-01-01T03:06:52.002       0  -6719.092336 -28929.061629   
...                          ...     ...           ...           ...   
1234089  2014-01-31T22:00:22.602     599 -21721.485878 -14048.557595   
1234090  2014-01-31T22:25:13.240     599 -23176.890569  -8712.016936   
1234091  2014-01-31T22:50:03.878     599 -23363.044794  -2906.071320   
1234092  2014-01-31T23:14:54.515     599 -22058.020262   3074.894039   
1234093  2014-01-31T23:39:45.153     599 -19076.969715   8807.476785   

                    z        Vx        Vy        Vz         x_sim  \
id                                                                  
0       -20728.353233 -0.908303 -3.808436 -2.022083  -8843.131454   
1       -24451.813271 -0.302590 -4.272617 -0.612796 -10555.500066   
2       -24238.280949  0.277435 -4.047522  0.723155 -10571.858472   
3       -20720.381279  0.715600 -3.373762  1.722115  -9149.620794   
4       -14938.907967  0.992507 -2.519732  2.344703  -6729.358857   
...               ...       ...       ...       ...           ...   
1234089   5277.807430 -1.351754  3.373418  0.004995 -20717.958996   
1234090   5153.371350 -0.575955  3.764450 -0.175109 -22673.444496   
1234091   4747.247386  0.351381  3.992943 -0.372198 -23461.830699   
1234092   4038.853542  1.421085  3.984793 -0.578849 -22858.679929   
1234093   3024.623998  2.587973  3.641717 -0.778817 -20656.328603   

                y_sim         z_sim    Vx_sim    Vy_sim    Vz_sim  \
id                                                                  
0        13138.221690 -20741.615306 -0.907527 -3.804930 -2.024133   
1         1649.289367 -24473.089556 -0.303704 -4.269816 -0.616468   
2       -10145.939908 -24271.169776  0.274880 -4.046788  0.718768   
3       -20618.200201 -20765.019094  0.712437 -3.375202  1.718306   
4       -28902.271436 -14992.399986  0.989382 -2.522618  2.342237   
...               ...           ...       ...       ...       ...   
1234089 -16245.240500   5250.939232 -1.653931  3.157321  0.079069   
1234090 -11192.339393   5243.608790 -0.945328  3.603371 -0.092202   
1234091  -5570.167175   4966.813869 -0.087089  3.912550 -0.281989   
1234092    373.249102   4396.055679  0.920162  4.021955 -0.485364   
1234093   6277.934683   3518.642806  2.050990  3.844021 -0.690707   

             delta_x      delta_y     delta_z  delta_Vx  delta_Vy  delta_Vz  
id                                                                           
0          12.692409    20.441543  -13.262073  0.000776  0.003506 -0.002050  
1          12.172318    29.543301  -21.276285 -0.001114  0.002801 -0.003673  
2           6.825572    34.527552  -32.888826 -0.002555  0.000734 -0.004387  
3          -1.368937    33.237259  -44.637815 -0.003163 -0.001440 -0.003809  
4         -10.266521    26.790192  -53.492019 -0.003125 -0.002887 -0.002466  
...              ...          ...         ...       ...       ...       ...  
1234089  1003.526882 -2196.682905  -26.868199 -0.302178 -0.216097  0.074074  
1234090   503.446074 -2480.322457   90.237441 -0.369372 -0.161079  0.082907  
1234091   -98.785905 -2664.095854  219.566483 -0.438470 -0.080393  0.090208  
1234092  -800.659667 -2701.644937  357.202137 -0.500923  0.037162  0.093485  
1234093 -1579.358888 -2529.542102  494.018808 -0.536983  0.202303  0.088109  

[649912 rows x 20 columns]

In [351]:
# x_num

for i, col in enumerate(['x_sim', 'y_sim', 'z_sim', 'Vx_sim', 'Vy_sim', 'Vz_sim']):
    full_train[col + '_num'] = 0
    arr = full_train[col + '_num'].values
    start = 0
    for sat_id in range(600):
        df = full_train[full_train.sat_id == sat_id]
        step = df.shape[0]
        idx_min = df[col].idxmin() % 24
        arr[start: start + step] = np.fromfunction(lambda i: (i + idx_min) % 24, (step, ))
        start += step
    full_train[col + '_num'] = arr
        

In [293]:
# давайте строить тренд по последним 5 предсказаниям (то есть мы будем делать следующее берём последние 5 
# значений интерполируем с помощью прямой, а далее смотрим чё получим)

[16 17 18 ...  3  4  5]


In [358]:
# x_num

for i, col in enumerate(['x_sim', 'y_sim', 'z_sim', 'Vx_sim', 'Vy_sim', 'Vz_sim']):
    full_test[col + '_num'] = 0
    arr = full_test[col + '_num'].values
    start = 0
    for sat_id in full_test.sat_id.unique():
        df = full_test[full_test.sat_id == sat_id]
        step = df.shape[0]
        idx_last = full_train[full_train.sat_id == sat_id][col + '_num'].iloc[-1] + 1
        arr[start: start + step] = np.fromfunction(lambda i: (i + idx_last) % 24, (step, ))
        start += step
    full_test[col + '_num'] = arr
        

In [277]:
full_train['x' + '_num'] = 0

In [297]:
full_train[full_train.sat_id == 0]

epoch  sat_id             x             y  \
id                                                                 
0    2014-01-01T00:00:00.000       0  -8855.823863  13117.780146   
1    2014-01-01T00:46:43.000       0 -10567.672384   1619.746066   
2    2014-01-01T01:33:26.001       0 -10578.684043 -10180.467460   
3    2014-01-01T02:20:09.001       0  -9148.251857 -20651.437460   
4    2014-01-01T03:06:52.002       0  -6719.092336 -28929.061629   
..                       ...     ...           ...           ...   
953  2014-01-31T20:27:33.474       0  17337.596150  -3224.996803   
954  2014-01-31T21:14:16.474       0  16849.590836   4217.959953   
955  2014-01-31T22:00:59.475       0  15667.981809  11481.446566   
956  2014-01-31T22:47:42.475       0  13754.838284  18199.705814   
957  2014-01-31T23:34:25.476       0  11090.021201  23908.338391   

                z        Vx        Vy        Vz         x_sim         y_sim  \
id                                                                            
0   -20728.353233 -0.908303 -3.808436 -2.022083  -8843.131454  13138.221690   
1   -24451.813271 -0.302590 -4.272617 -0.612796 -10555.500066   1649.289367   
2   -24238.280949  0.277435 -4.047522  0.723155 -10571.858472 -10145.939908   
3   -20720.381279  0.715600 -3.373762  1.722115  -9149.620794 -20618.200201   
4   -14938.907967  0.992507 -2.519732  2.344703  -6729.358857 -28902.271436   
..            ...       ...       ...       ...           ...           ...   
953  40025.071742 -0.055615  2.650511 -0.222561  15425.677762  12387.078210   
954  38636.167298 -0.295282  2.642711 -0.774030  13419.744899  19007.658296   
955  35656.909015 -0.550136  2.518368 -1.356292  10662.661170  24548.177490   
956  31013.052037 -0.816256  2.247835 -1.959266   7182.757625  28395.590633   
957  24674.831301 -1.084189  1.790199 -2.559726   3099.591832  29798.085757   

     ...       delta_z  delta_Vx  delta_Vy  delta_Vz  x_num  Vx_num  y_num  \
id   ...                                                                     
0    ...    -13.262073  0.000776  0.003506 -0.002050      4       0      9   
1    ...    -21.276285 -0.001114  0.002801 -0.003673      5       1     10   
2    ...    -32.888826 -0.002555  0.000734 -0.004387      6       2     11   
3    ...    -44.637815 -0.003163 -0.001440 -0.003809      7       3     12   
4    ...    -53.492019 -0.003125 -0.002887 -0.002466      8       4     13   
..   ...           ...       ...       ...       ...    ...     ...    ...   
953  ...  -4879.299912 -0.527231 -0.156437 -1.211385     21      17      2   
954  ...  -8355.689969 -0.554339 -0.441210 -1.264989     22      18      3   
955  ... -11936.165799 -0.566125 -0.802939 -1.280543     23      19      4   
956  ... -15459.066758 -0.543839 -1.263139 -1.213983      0      20      5   
957  ... -18591.737280 -0.452746 -1.823714 -0.985042      1      21      6   

     Vy_num  z_num  Vz_num  
id                          
0         1      1       0  
1         2      2       1  
2         3      3       2  
3         4      4       3  
4         5      5       4  
..      ...    ...     ...  
953      18     18      17  
954      19     19      18  
955      20     20      19  
956      21     21      20  
957      22     22      21  

[958 rows x 26 columns]

In [310]:
for col_name in ['x', 'y', 'z', 'Vx', 'Vy', 'Vz']:
    full_test[col_name] = 0.0

In [311]:
full_test.dtypes

sat_id          int64
epoch          object
x_sim         float64
y_sim         float64
z_sim         float64
Vx_sim        float64
Vy_sim        float64
Vz_sim        float64
x_sim_num       int64
y_sim_num       int64
z_sim_num       int64
Vx_sim_num      int64
Vy_sim_num      int64
Vz_sim_num      int64
x             float64
y             float64
z             float64
Vx            float64
Vy            float64
Vz            float64
dtype: object

In [364]:
width = 4
for sat_id in tqdm(full_test.sat_id.unique()):
    df1_train = full_train[full_train.sat_id == sat_id]
    df1_test =  full_test[full_test.sat_id == sat_id]
    for col in tqdm(['x', 'y', 'z', 'Vx', 'Vy', 'Vz'], leave=False):
        for i in range(24):
            df2_train = df1_train[df1_train[col + '_num'] == i]
            df2_test = df1_test[df1_test[col + '_sim_num'] == i]
            lin_model = LinearRegression()
            X_train = df2_train.reset_index()['id'].values[-width:].reshape(-1, 1)
            y_train = df2_train[col].values[-width:]
            lin_model.fit(X_train, y_train)
            X_test = df2_test.reset_index()['id'].values.reshape(-1, 1)
            y_test = lin_model.predict(X_test)
            full_test.loc[X_test.ravel(), col] = y_test

In [362]:
# интерполяция по производной !!! просто интересно было псомотерть


sat_id = 2
fig = make_subplots(rows=3, cols=2,
                    subplot_titles=['x', 'Vx', 'y', 'Vy', 'z', 'Vz'])

for i, real_col_name in enumerate(['x', 'y', 'z', 'Vx', 'Vy', 'Vz']):
    row, col = i % 3 + 1, i // 3 + 1
    sim_col_name = real_col_name + '_sim'
    fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                             y=full_test[full_test.sat_id == sat_id][real_col_name],
                             name="Estimated " + real_col_name,
                             ), row=row, col=col)

    fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                             y=full_test[full_test.sat_id == sat_id][sim_col_name],
                             name="Simulation " + real_col_name,
                             ), row=row, col=col)

    fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                             y=full_test[full_test.sat_id == sat_id][sim_col_name],
                             name="Sim_test " + real_col_name,
                             ), row=row, col=col)
    fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                             y=full_train[full_train.sat_id == sat_id][real_col_name],
                             name="Real " + real_col_name,
                             ), row=row, col=col)

    fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                             y=full_train[full_train.sat_id == sat_id][sim_col_name],
                             name="Simulation " + real_col_name,
                             ), row=row, col=col)

fig.show()

In [367]:
# отрисовка нужного рядя для анализа

figure = plt.figure(figsize=(10, 5))


sat_id = 299
real_col_name = 'x'
sim_col_name = real_col_name + '_sim'

fig = go.Figure()
fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                             y=full_test[full_test.sat_id == sat_id][real_col_name],
                             name="Estimated " + real_col_name,
                             ))

fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                         y=full_test[full_test.sat_id == sat_id][sim_col_name],
                         name="Simulation " + real_col_name,
                         ))

fig.add_trace(go.Scatter(x=full_test[full_test.sat_id == sat_id].epoch,
                         y=full_test[full_test.sat_id == sat_id][sim_col_name],
                         name="Sim_test " + real_col_name,
                         ))
fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][real_col_name],
                         name="Real " + real_col_name,
                         ))

fig.add_trace(go.Scatter(x=full_train[full_train.sat_id == sat_id].epoch,
                         y=full_train[full_train.sat_id == sat_id][sim_col_name],
                         name="Simulation " + real_col_name,
                         ))

fig.update_layout(title_text='Time Series for ' + real_col_name,
                  xaxis_rangeslider_visible=True,
                  yaxis_title=real_col_name)
fig.show()

<Figure size 720x360 with 0 Axes>

In [359]:
full_train[full_train.sat_id==25]

epoch  sat_id             x             y  \
id                                                                   
49170  2014-01-01T00:00:00.000      25 -11688.343088   3090.573912   
49171  2014-01-01T00:59:34.600      25 -20982.661770  -7500.870948   
49172  2014-01-01T01:59:09.201      25 -21066.158338 -15225.222626   
49173  2014-01-01T02:58:43.801      25 -16576.488169 -19858.027685   
49174  2014-01-01T03:58:18.402      25 -10198.800998 -22336.917974   
...                        ...     ...           ...           ...   
49917  2014-01-31T19:44:37.348      25 -20225.821660  -5619.419185   
49918  2014-01-31T20:44:11.948      25 -21737.469873 -14000.448306   
49919  2014-01-31T21:43:46.549      25 -17916.839553 -19188.822806   
49920  2014-01-31T22:43:21.149      25 -11839.155071 -22076.441573   
49921  2014-01-31T23:42:55.750      25  -4866.859085 -23373.830955   

                  z        Vx        Vy        Vz         x_sim         y_sim  \
id                                                                              
49170 -14579.251996 -4.085267 -2.990730  2.641215 -11650.269626   3150.034596   
49171  -1371.134347 -1.093479 -2.658589  4.238782 -20975.805340  -7472.648284   
49172  13248.400649  0.796565 -1.682992  3.792120 -21089.106322 -15238.766260   
49173  25397.656639  1.598034 -0.956059  3.007305 -16611.380403 -19901.873152   
49174  34858.999568  1.919541 -0.461334  2.306414 -10235.711415 -22399.361509   
...             ...       ...       ...       ...           ...           ...   
49917  -4213.549946 -1.631949 -2.817845  4.141672 -16767.029237 -19896.083254   
49918  10561.363158  0.525654 -1.861416  3.914561 -10403.354296 -22392.440561   
49919  23203.592572  1.475436 -1.088870  3.148240  -3320.030077 -23415.660585   
49920  33143.594953  1.866073 -0.559500  2.431938   3932.729446 -23368.127513   
49921  40726.903135  2.007002 -0.186657  1.828817  11059.298961 -22510.402903   

       ...  y_num  Vy_num  z_num  Vz_num  x_sim_num  y_sim_num  z_sim_num  \
id     ...                                                                  
49170  ...      2      18     17      14         19         23         17   
49171  ...      3      19     18      15         20          0         18   
49172  ...      4      20     19      16         21          1         19   
49173  ...      5      21     20      17         22          2         20   
49174  ...      6      22     21      18         23          3         21   
...    ...    ...     ...    ...     ...        ...        ...        ...   
49917  ...      5      21     20      17         22          2         20   
49918  ...      6      22     21      18         23          3         21   
49919  ...      7      23     22      19          0          4         22   
49920  ...      8       0     23      20          1          5         23   
49921  ...      9       1      0      21          2          6          0   

       Vx_sim_num  Vy_sim_num  Vz_sim_num  
id                                         
49170          17          18          14  
49171          18          19          15  
49172          19          20          16  
49173          20          21          17  
49174          21          22          18  
...           ...         ...         ...  
49917          20          21          17  
49918          21          22          18  
49919          22          23          19  
49920          23           0          20  
49921           0           1          21  

[752 rows x 32 columns]

In [360]:
full_test[full_test.sat_id==25]

sat_id                    epoch         x_sim         y_sim  \
id                                                                   
49922      25  2014-02-01T00:42:30.350  17881.788791 -21020.614114   
49923      25  2014-02-01T01:42:04.951  24280.268592 -19027.284588   
49924      25  2014-02-01T02:41:39.551  30163.781753 -16628.073381   
49925      25  2014-02-01T03:41:14.152  35454.702280 -13901.131644   
49926      25  2014-02-01T04:40:48.752  40079.169994 -10912.528685   
...       ...                      ...           ...           ...   
50592      25  2014-02-28T15:59:43.462   3625.768652 -23365.560962   
50593      25  2014-02-28T16:59:18.062  10764.845101 -22548.691539   
50594      25  2014-02-28T17:58:52.663  17607.796813 -21098.066837   
50595      25  2014-02-28T18:58:27.263  24032.348690 -19140.903939   
50596      25  2014-02-28T19:58:01.864  29945.529807 -16774.079569   

              z_sim    Vx_sim    Vy_sim    Vz_sim  x_sim_num  y_sim_num  \
id                                                                        
49922  53027.180656  1.854066  0.492290  0.417952          3          7   
49923  53910.194434  1.721820  0.618382  0.081554          4          8   
49924  53644.976519  1.566537  0.720300 -0.225703          5          9   
49925  52323.423429  1.390426  0.802331 -0.510359          6         10   
49926  50017.226128  1.193506  0.867040 -0.777269          7         11   
...             ...       ...       ...       ...        ...        ...   
50592  47336.805443  2.023826  0.124890  1.213806          1          5   
50593  50898.856440  1.962545  0.323943  0.788654          2          6   
50594  53034.599255  1.860726  0.481700  0.413452          3          7   
50595  53899.765735  1.729747  0.608758  0.076089          4          8   
50596  53613.062436  1.575205  0.711814 -0.232235          5          9   

       z_sim_num  Vx_sim_num  Vy_sim_num  Vz_sim_num             x  \
id                                                                   
49922          1           1           2          22  47352.761767   
49923          2           2           3          23  42922.520385   
49924          3           3           4           0  35961.959347   
49925          4           4           5           1  24577.202511   
49926          5           5           6           2   6645.484526   
...          ...         ...         ...         ...           ...   
50592         23          23           0          20  55682.975053   
50593          0           0           1          21  58739.175052   
50594          1           1           2          22  61256.148096   
50595          2           2           3          23  63300.748079   
50596          3           3           4           0  64321.339682   

                  y             z        Vx        Vy        Vz  
id                                                               
49922  11643.580997 -15217.764601 -4.082756 -0.173856 -2.675783  
49923  14448.078876 -21813.820423 -5.622110 -1.888773 -0.562993  
49924  16674.515802 -17692.927115 -4.322475 -3.154409  2.793884  
49925  17588.890277  -3954.602836 -1.275740 -2.785112  4.337412  
49926  14143.227351  11094.361535  0.694618 -1.801921  3.924172  
...             ...           ...       ...       ...       ...  
50592  -1743.581572  21569.733150  0.485340  1.779582 -2.981093  
50593   2598.835053   8331.734393 -0.119301  2.432556 -4.660911  
50594   7414.476194 -13829.882727 -3.663411  2.475461 -7.368292  
50595  13106.264215 -38930.103504 -9.374870 -0.777384 -5.435048  
50596  20565.991543 -46685.763042 -9.419857 -4.362420  1.316804  

[675 rows x 20 columns]

In [371]:
full_test[['x', 'y', 'z', 'Vx', 'Vy', 'Vz']].to_csv('submission.csv', index_label='id')